<a href="https://colab.research.google.com/github/joacorapela/svGPFA/blob/master/doEstimateAndPlot.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Contents:
- [1 Estimation](#estimation)
- [2 Plotting](#plotting)
- [3 GOF](#GOF)

# Clone repository

In [ ]:
!rm -rf svGPFA/
!git clone https://github.com/joacorapela/svGPFA.git
%pip install git+file:///content/svGPFA
%cd svGPFA/doc/ipynb

Cloning into 'svGPFA'...
remote: Enumerating objects: 9372, done.
remote: Counting objects: 100% (235/235), done.
remote: Compressing objects: 100% (140/140), done.
remote: Total 9372 (delta 118), reused 186 (delta 81), pack-reused 9137
Receiving objects: 100% (9372/9372), 248.51 MiB | 14.84 MiB/s, done.
Resolving deltas: 100% (5659/5659), done.
Checking out files: 100% (115/115), done.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning file:///content/svGPFA to /tmp/pip-req-build-i2r2r9go
  Running command git clone -q file:///content/svGPFA /tmp/pip-req-build-i2r2r9go
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
    Preparing wheel metadata ... done
/content/svGPFA/doc/ipynb


# 1 Estimation <a class="anchor" id="estimation"></a>

## 1.1 Import requirements

In [ ]:
import time
import torch
import pickle
import plotly.colors

import svGPFA.stats.kernels
import svGPFA.stats.svGPFAModelFactory
import svGPFA.stats.svEM
import svGPFA.utils.miscUtils
import svGPFA.utils.initUtils
import gcnu_common.stats.pointProcesses.tests

## 1.2 Set parameters

In [ ]:
n_latents = 2                                      # number of latents
n_neurons = 100                                    # number of neurons
n_trials = 15                                      # number of trials
prior_cov_reg_param = 1e-5                         # prior covariance regularization parameter
trials_start_time = 0.0                             # trial start time
trials_end_time = 1.0                               # trial end time
em_max_iter = 30                                   # maximum number of EM iterations

## 1.3 Load spikes times

In [ ]:
simResFilename = "../../examples/data/32451751_simRes.pickle" # simulation results filename
with open(simResFilename, "rb") as f:
    simRes = pickle.load(f)
spikes_times = simRes["spikes"]

## 1.4 Create initial values of parameters

In [ ]:
# refer to this https://joacorapela.github.io/svGPFA/params.html# for a full description
# of different ways of specify svGPFA parameters

# get default params
default_params = svGPFA.utils.initUtils.getDefaultParamsDict(
    n_neurons=n_neurons, n_trials=n_trials, n_latents=n_latents,
    trials_start_time=trials_start_time, trials_end_time=trials_end_time,
    em_max_iter=em_max_iter, prior_cov_reg_param=prior_cov_reg_param)

# build the svGPFA parameters from their default and dynamic specifications
initial_params, quad_params, kernels_types, optim_params = \
    svGPFA.utils.initUtils.getParams(
        n_trials=n_trials, n_neurons=n_neurons,
        default_params=default_params)
kernels_params0 = initial_params["svPosteriorOnLatents"]["kernelsMatricesStore"]["kernelsParams0"]
optim_method = optim_params["optim_method"]
prior_cov_reg_param = optim_params["prior_cov_reg_param"]

Extracted default_params[model_structure_params][n_latents]=2
Extracted default_params[optim_params][n_quad]=200
Extracted default_params[ind_points_params0][n_ind_points]=10
Extracted c0 from default
Extracted d0 from default
Extracted trials_start_times from default
Extracted trials_end_times from default
Extracted k_type=exponentialQuadratic and k_lengthsale0=1.0 from default
Extracted ind_points_locs0_layout=equidistant from default
Extracted variational_mean0 from default
Extracted variational_cov0 from default
Extracted default_params[optim_params][n_quad]=200
Extracted default_params[optim_params][prior_cov_reg_param]=1e-05
Extracted default_params[optim_params][optim_method]=ecm
Extracted default_params[optim_params][em_max_iter]=30
Extracted default_params[optim_params][verbose]=True
Extracted default_params[optim_params][estep_estimate]=True
Extracted default_params[optim_params][estep_max_iter]=20
Extracted default_params[optim_params][estep_lr]=1.0
Extracted default_params[

## 1.5 Create a model and set its initial parameters

In [ ]:
kernels = svGPFA.utils.miscUtils.buildKernels(
    kernels_types=kernels_types, kernels_params=kernels_params0)

kernelMatrixInvMethod = svGPFA.stats.svGPFAModelFactory.kernelMatrixInvChol
indPointsCovRep = svGPFA.stats.svGPFAModelFactory.indPointsCovChol
model = svGPFA.stats.svGPFAModelFactory.SVGPFAModelFactory.buildModelPyTorch(
    conditionalDist=svGPFA.stats.svGPFAModelFactory.PointProcess,
    linkFunction=svGPFA.stats.svGPFAModelFactory.ExponentialLink,
    embeddingType=svGPFA.stats.svGPFAModelFactory.LinearEmbedding,
    kernels=kernels, kernelMatrixInvMethod=kernelMatrixInvMethod,
    indPointsCovRep=indPointsCovRep)
model.setInitialParamsAndData(
    measurements=spikes_times,
    initialParams=initial_params,
    eLLCalculationParams=quad_params,
    priorCovRegParam=prior_cov_reg_param)

## 1.7 Maximize the Lower Bound
<span style="color:red">(Warning: with the parameters above, this step takes around 10 minutes)</span>

In [ ]:
svEM = svGPFA.stats.svEM.SVEM_PyTorch()
tic = time.perf_counter()
lowerBoundHist, elapsedTimeHist, terminationInfo, iterationsModelParams = \
    svEM.maximize(model=model, optim_params=optim_params, method=optim_method)
toc = time.perf_counter()
print(f"Elapsed time {toc - tic:0.4f} seconds")

Iteration 01, estep start: -inf
Iteration 01, estep end: 134850.667932, niter: 20, nfeval: 25
Iteration 01, mstep_embedding start: 134850.667932
Iteration 01, mstep_embedding end: 896872.432917, niter: 18, nfeval: 25
Iteration 01, mstep_kernels start: 896872.432917
Iteration 01, mstep_kernels end: 895600.242311, niter: 13, nfeval: 17
Iteration 01, mstep_indpointslocs start: 895600.242311
Iteration 01, mstep_indpointslocs end: 925653.138619, niter: 14, nfeval: 27
Iteration 02, estep start: 925653.138619
Iteration 02, estep end: 959767.350220, niter: 20, nfeval: 22
Iteration 02, mstep_embedding start: 959767.350220
Iteration 02, mstep_embedding end: 992531.900372, niter: 20, nfeval: 21
Iteration 02, mstep_kernels start: 992531.900372
Iteration 02, mstep_kernels end: 991439.242256, niter: 8, nfeval: 11
Iteration 02, mstep_indpointslocs start: 991439.242256
Iteration 02, mstep_indpointslocs end: 994556.050896, niter: 19, nfeval: 25
Iteration 03, estep start: 994556.050896
Iteration 03, est

# 2 Plotting <a class="anchor" id="plotting"></a>

## 2.1 Setup for plotting

In [ ]:
import numpy as np
import pandas as pd
import sklearn.metrics
import svGPFA.plot.plotUtilsPlotly

trials_colors = plotly.colors.n_colors('rgb(0, 0, 255)', 'rgb(255, 0, 0)', n_trials, colortype = 'rgb')

## 2.2 Lower bound history

In [ ]:
fig = svGPFA.plot.plotUtilsPlotly.getPlotLowerBoundHist(lowerBoundHist=lowerBoundHist)
fig.show()

## 2.3 Set neuron, latent and times to plot

In [ ]:
neuronToPlot = 0
latentToPlot = 0
sampling_rate = 1000.0 # Hz
trials_times = torch.arange(trials_start_time, trials_end_time, 1.0/sampling_rate)

## 2.4 Latents

In [ ]:
# plot estimated latent across trials
testMuK, testVarK = model.predictLatents(times=trials_times)
indPointsLocs = model.getIndPointsLocs()
fig = svGPFA.plot.plotUtilsPlotly.getPlotLatentAcrossTrials(times=trials_times.numpy(), latentsMeans=testMuK, latentsSTDs=torch.sqrt(testVarK), indPointsLocs=indPointsLocs, latentToPlot=latentToPlot, trials_colors=trials_colors, xlabel="Time (msec)")
fig.show()

## 2.5 Embedding

In [ ]:
embeddingMeans, embeddingVars = model.predictEmbedding(times=trials_times)
embeddingMeans = embeddingMeans.detach().numpy()
embeddingVars = embeddingVars.detach().numpy()
title = "Neuron {:d}".format(neuronToPlot)
fig = svGPFA.plot.plotUtilsPlotly.getPlotEmbeddingAcrossTrials(times=trials_times.numpy(), embeddingsMeans=embeddingMeans[:,:,neuronToPlot], embeddingsSTDs=np.sqrt(embeddingVars[:,:,neuronToPlot]), trials_colors=trials_colors, title=title)
fig.show()

## 2.6 CIFs

In [ ]:

with torch.no_grad():
    ePosCIFValues = model.computeExpectedPosteriorCIFs(times=trials_times)
fig = svGPFA.plot.plotUtilsPlotly.getPlotCIFsOneNeuronAllTrials(times=trials_times, cif_values=ePosCIFValues, neuron_index=neuronToPlot, trials_colors=trials_colors)                                                                                                                                      
fig.show()

## 2.7 Embedding parameters

In [ ]:
estimatedC, estimatedD = model.getSVEmbeddingParams()
fig = svGPFA.plot.plotUtilsPlotly.getPlotEmbeddingParams(C=estimatedC.numpy(), d=estimatedD.numpy())
fig.show()

## 2.8 Kernels parameters

In [ ]:
kernelsParams = model.getKernelsParams()
kernelsTypes = [type(kernel).__name__ for kernel in model.getKernels()]
fig = svGPFA.plot.plotUtilsPlotly.getPlotKernelsParams(
    kernelsTypes=kernelsTypes, kernelsParams=kernelsParams)
fig.show()

# 3 Goodness of fit (GOF) tests <a class="anchor" id="GOF"></a>


## 3.1 Set trial and neuron for GOF assesment

In [ ]:
trialForGOF = 0
neuronForGOF = 0

## 3.2 KS time-rescaling GOF test

In [ ]:
ksTest_gamma = 20                                 # number of simulations for the KS test numerical correction
with torch.no_grad():
    epmcifValues = model.computeExpectedPosteriorCIFs(times=trials_times)
cifValuesKS = epmcifValues[trialForGOF][neuronForGOF]
spikesTimesKS = spikes_times[trialForGOF][neuronForGOF]
diffECDFsX, diffECDFsY, estECDFx, estECDFy, simECDFx, simECDFy, cb = gcnu_common.stats.pointProcesses.tests.KSTestTimeRescalingNumericalCorrection(spikesTimes=spikesTimesKS, cifTimes=trials_times, cifValues=cifValuesKS, gamma=ksTest_gamma)
title = "Trial {:d}, Neuron {:d}".format(trialForGOF, neuronForGOF)
fig = svGPFA.plot.plotUtilsPlotly.getPlotResKSTestTimeRescalingNumericalCorrection(diffECDFsX=diffECDFsX, diffECDFsY=diffECDFsY, estECDFx=estECDFx, estECDFy=estECDFy, simECDFx=simECDFx, simECDFy=simECDFy, cb=cb, title=title)
fig.show()

Processing given ISIs


/usr/local/lib/python3.7/dist-packages/gcnu_common/stats/pointProcesses/tests.py:33: UserWarning:

Found more than one spike in 12 bins



Processing iter 0/19


/usr/local/lib/python3.7/dist-packages/gcnu_common/stats/pointProcesses/tests.py:33: UserWarning:

Found more than one spike in 14 bins



Processing iter 1/19


...

/usr/local/lib/python3.7/dist-packages/gcnu_common/stats/pointProcesses/tests.py:33: UserWarning:

Found more than one spike in 11 bins



Processing iter 12/19
Processing iter 13/19
Processing iter 14/19
Processing iter 15/19


/usr/local/lib/python3.7/dist-packages/gcnu_common/stats/pointProcesses/tests.py:33: UserWarning:

Found more than one spike in 19 bins



Processing iter 16/19
Processing iter 17/19
Processing iter 18/19
Processing iter 19/19


/usr/local/lib/python3.7/dist-packages/gcnu_common/stats/pointProcesses/tests.py:33: UserWarning:

Found more than one spike in 21 bins



## 3.3 ROC predictive analysis

In [ ]:
dt = (trials_times[1] - trials_times[0]).item()
pk = cifValuesKS.detach().numpy() * dt
bins = pd.interval_range(start=trials_start_time, end=trials_end_time, periods=len(pk))
cutRes, _ = pd.cut(spikesTimesKS.tolist(), bins=bins, retbins=True)
Y = cutRes.value_counts().values
fpr, tpr, thresholds = sklearn.metrics.roc_curve(Y, pk, pos_label=1)
roc_auc = sklearn.metrics.auc(fpr, tpr)
title = "Trial {:d}, Neuron {:d}".format(trialForGOF, neuronForGOF)
fig = svGPFA.plot.plotUtilsPlotly.getPlotResROCAnalysis(fpr=fpr, tpr=tpr, auc=roc_auc, title=title)
fig.show()